# Import packages

In [1]:
import collections
import copy
import json
import multiprocessing
import math
import os
import random
import shutil
import subprocess

import aiohttp
import tqdm

import pandas as pd

In [2]:
DATA_REPOS = 'data/repos/'
DATA_JS_FILES = 'data/js_files/'
DATA_FUNCS = 'data/funcs/'
DATA_OBFUSCATED_FUNCS = 'data/obfuscated_funcs/'
DATA_AST_FEATURES = 'data/ast_features/'
DATA_FEATURES_JSON = 'data/features.json'

In [3]:
def create_dir_if_not_exists(dir_: str):
    try:
        os.mkdir(dir_)
    except Exception as e:
        print(e)

# Download github projects

Get top github projects with language assigned 'Javascript' sorted by stars count

In [31]:
GITHUB_SEARCH_URI = 'https://api.github.com/search/repositories?q=language:JavaScript' + \
      '&sort=stars&order=desc&page={}&per_page=100'


github_projects = set()


async with aiohttp.ClientSession() as session:
    i = 0
    while len(github_projects) < 500:
        print(GITHUB_SEARCH_URI.format(i))
        
        async with session.get(GITHUB_SEARCH_URI.format(i)) as resp:
            search_results = await resp.json()
            print(search_results)
            for project in search_results['items']:
                github_projects.add((project['full_name'], project['html_url']))
        i += 1


github_projects = list(github_projects)


for project in github_projects:
    print(project[0], ', ', project[1])


https://api.github.com/search/repositories?q=language:JavaScript&sort=stars&order=desc&page=0&per_page=100
{'total_count': 15415586, 'incomplete_results': True, 'items': [{'id': 11730342, 'node_id': 'MDEwOlJlcG9zaXRvcnkxMTczMDM0Mg==', 'name': 'vue', 'full_name': 'vuejs/vue', 'private': False, 'owner': {'login': 'vuejs', 'id': 6128107, 'node_id': 'MDEyOk9yZ2FuaXphdGlvbjYxMjgxMDc=', 'avatar_url': 'https://avatars.githubusercontent.com/u/6128107?v=4', 'gravatar_id': '', 'url': 'https://api.github.com/users/vuejs', 'html_url': 'https://github.com/vuejs', 'followers_url': 'https://api.github.com/users/vuejs/followers', 'following_url': 'https://api.github.com/users/vuejs/following{/other_user}', 'gists_url': 'https://api.github.com/users/vuejs/gists{/gist_id}', 'starred_url': 'https://api.github.com/users/vuejs/starred{/owner}{/repo}', 'subscriptions_url': 'https://api.github.com/users/vuejs/subscriptions', 'organizations_url': 'https://api.github.com/users/vuejs/orgs', 'repos_url': 'https:

{'total_count': 15034442, 'incomplete_results': True, 'items': [{'id': 11730342, 'node_id': 'MDEwOlJlcG9zaXRvcnkxMTczMDM0Mg==', 'name': 'vue', 'full_name': 'vuejs/vue', 'private': False, 'owner': {'login': 'vuejs', 'id': 6128107, 'node_id': 'MDEyOk9yZ2FuaXphdGlvbjYxMjgxMDc=', 'avatar_url': 'https://avatars.githubusercontent.com/u/6128107?v=4', 'gravatar_id': '', 'url': 'https://api.github.com/users/vuejs', 'html_url': 'https://github.com/vuejs', 'followers_url': 'https://api.github.com/users/vuejs/followers', 'following_url': 'https://api.github.com/users/vuejs/following{/other_user}', 'gists_url': 'https://api.github.com/users/vuejs/gists{/gist_id}', 'starred_url': 'https://api.github.com/users/vuejs/starred{/owner}{/repo}', 'subscriptions_url': 'https://api.github.com/users/vuejs/subscriptions', 'organizations_url': 'https://api.github.com/users/vuejs/orgs', 'repos_url': 'https://api.github.com/users/vuejs/repos', 'events_url': 'https://api.github.com/users/vuejs/events{/privacy}', '

{'total_count': 13895938, 'incomplete_results': True, 'items': [{'id': 79779269, 'node_id': 'MDEwOlJlcG9zaXRvcnk3OTc3OTI2OQ==', 'name': 'vant-weapp', 'full_name': 'youzan/vant-weapp', 'private': False, 'owner': {'login': 'youzan', 'id': 11404085, 'node_id': 'MDEyOk9yZ2FuaXphdGlvbjExNDA0MDg1', 'avatar_url': 'https://avatars.githubusercontent.com/u/11404085?v=4', 'gravatar_id': '', 'url': 'https://api.github.com/users/youzan', 'html_url': 'https://github.com/youzan', 'followers_url': 'https://api.github.com/users/youzan/followers', 'following_url': 'https://api.github.com/users/youzan/following{/other_user}', 'gists_url': 'https://api.github.com/users/youzan/gists{/gist_id}', 'starred_url': 'https://api.github.com/users/youzan/starred{/owner}{/repo}', 'subscriptions_url': 'https://api.github.com/users/youzan/subscriptions', 'organizations_url': 'https://api.github.com/users/youzan/orgs', 'repos_url': 'https://api.github.com/users/youzan/repos', 'events_url': 'https://api.github.com/users

{'total_count': 15355944, 'incomplete_results': True, 'items': [{'id': 18405734, 'node_id': 'MDEwOlJlcG9zaXRvcnkxODQwNTczNA==', 'name': 'smartcrop.js', 'full_name': 'jwagner/smartcrop.js', 'private': False, 'owner': {'login': 'jwagner', 'id': 293536, 'node_id': 'MDQ6VXNlcjI5MzUzNg==', 'avatar_url': 'https://avatars.githubusercontent.com/u/293536?v=4', 'gravatar_id': '', 'url': 'https://api.github.com/users/jwagner', 'html_url': 'https://github.com/jwagner', 'followers_url': 'https://api.github.com/users/jwagner/followers', 'following_url': 'https://api.github.com/users/jwagner/following{/other_user}', 'gists_url': 'https://api.github.com/users/jwagner/gists{/gist_id}', 'starred_url': 'https://api.github.com/users/jwagner/starred{/owner}{/repo}', 'subscriptions_url': 'https://api.github.com/users/jwagner/subscriptions', 'organizations_url': 'https://api.github.com/users/jwagner/orgs', 'repos_url': 'https://api.github.com/users/jwagner/repos', 'events_url': 'https://api.github.com/users/

{'total_count': 15404761, 'incomplete_results': True, 'items': [{'id': 76289797, 'node_id': 'MDEwOlJlcG9zaXRvcnk3NjI4OTc5Nw==', 'name': 'react-360', 'full_name': 'facebookarchive/react-360', 'private': False, 'owner': {'login': 'facebookarchive', 'id': 7560860, 'node_id': 'MDEyOk9yZ2FuaXphdGlvbjc1NjA4NjA=', 'avatar_url': 'https://avatars.githubusercontent.com/u/7560860?v=4', 'gravatar_id': '', 'url': 'https://api.github.com/users/facebookarchive', 'html_url': 'https://github.com/facebookarchive', 'followers_url': 'https://api.github.com/users/facebookarchive/followers', 'following_url': 'https://api.github.com/users/facebookarchive/following{/other_user}', 'gists_url': 'https://api.github.com/users/facebookarchive/gists{/gist_id}', 'starred_url': 'https://api.github.com/users/facebookarchive/starred{/owner}{/repo}', 'subscriptions_url': 'https://api.github.com/users/facebookarchive/subscriptions', 'organizations_url': 'https://api.github.com/users/facebookarchive/orgs', 'repos_url': 'h

{'total_count': 16008334, 'incomplete_results': True, 'items': [{'id': 19943999, 'node_id': 'MDEwOlJlcG9zaXRvcnkxOTk0Mzk5OQ==', 'name': 'AndroidAssetStudio', 'full_name': 'romannurik/AndroidAssetStudio', 'private': False, 'owner': {'login': 'romannurik', 'id': 100155, 'node_id': 'MDQ6VXNlcjEwMDE1NQ==', 'avatar_url': 'https://avatars.githubusercontent.com/u/100155?v=4', 'gravatar_id': '', 'url': 'https://api.github.com/users/romannurik', 'html_url': 'https://github.com/romannurik', 'followers_url': 'https://api.github.com/users/romannurik/followers', 'following_url': 'https://api.github.com/users/romannurik/following{/other_user}', 'gists_url': 'https://api.github.com/users/romannurik/gists{/gist_id}', 'starred_url': 'https://api.github.com/users/romannurik/starred{/owner}{/repo}', 'subscriptions_url': 'https://api.github.com/users/romannurik/subscriptions', 'organizations_url': 'https://api.github.com/users/romannurik/orgs', 'repos_url': 'https://api.github.com/users/romannurik/repos',

Create `data/repos/` directory 

In [33]:
create_dir_if_not_exists(DATA_REPOS)

Clone repositories

In [35]:
# with open('repositories.tsv', 'w') as f:
#     f.write(f'name\turi\n')
#     for project in github_projects:
#         f.write(f'{project[0]}\t{project[1]}\n')

In [36]:
for project in github_projects:
    ! cd {DATA_REPOS} && git clone {project[1]} --depth 1


Cloning into 'trilium'...
remote: Enumerating objects: 1011, done.
remote: Counting objects: 100% (1011/1011), done.
remote: Compressing objects: 100% (843/843), done.
remote: Total 1011 (delta 98), reused 468 (delta 38), pack-reused 0
Receiving objects: 100% (1011/1011), 10.90 MiB | 3.24 MiB/s, done.
Resolving deltas: 100% (98/98), done.
Cloning into 'gmaps'...
remote: Enumerating objects: 96, done.
remote: Counting objects: 100% (96/96), done.
remote: Compressing objects: 100% (90/90), done.
remote: Total 96 (delta 11), reused 45 (delta 4), pack-reused 0
Receiving objects: 100% (96/96), 138.28 KiB | 1.42 MiB/s, done.
Resolving deltas: 100% (11/11), done.
Cloning into 'brunch'...
remote: Enumerating objects: 73, done.
remote: Counting objects: 100% (73/73), done.
remote: Compressing objects: 100% (62/62), done.
remote: Total 73 (delta 1), reused 29 (delta 1), pack-reused 0
Receiving objects: 100% (73/73), 76.81 KiB | 854.00 KiB/s, done.
Resolving deltas: 100% (1/1), done.
Cloning into

remote: Total 674 (delta 70), reused 419 (delta 30), pack-reused 0
Receiving objects: 100% (674/674), 2.34 MiB | 3.76 MiB/s, done.
Resolving deltas: 100% (70/70), done.
Cloning into 'lib-flexible'...
remote: Enumerating objects: 8, done.
remote: Counting objects: 100% (8/8), done.
remote: Compressing objects: 100% (8/8), done.
Receiving objects: 100% (8/8), done.
remote: Total 8 (delta 0), reused 4 (delta 0), pack-reused 0
Cloning into 'leonsans'...
remote: Enumerating objects: 74, done.
remote: Counting objects: 100% (74/74), done.
remote: Compressing objects: 100% (61/61), done.
remote: Total 74 (delta 16), reused 55 (delta 10), pack-reused 0
Receiving objects: 100% (74/74), 264.98 KiB | 1.63 MiB/s, done.
Resolving deltas: 100% (16/16), done.
Cloning into 'react-draggable'...
remote: Enumerating objects: 41, done.
remote: Counting objects: 100% (41/41), done.
remote: Compressing objects: 100% (38/38), done.
remote: Total 41 (delta 0), reused 10 (delta 0), pack-reused 0
Receiving obje

Cloning into 'faker.js'...
remote: Enumerating objects: 2010, done.
remote: Counting objects: 100% (2010/2010), done.
remote: Compressing objects: 100% (1715/1715), done.
remote: Total 2010 (delta 294), reused 1634 (delta 183), pack-reused 0
Receiving objects: 100% (2010/2010), 3.08 MiB | 5.03 MiB/s, done.
Resolving deltas: 100% (294/294), done.
Cloning into 'lazy.js'...
remote: Enumerating objects: 144, done.
remote: Counting objects: 100% (144/144), done.
remote: Compressing objects: 100% (130/130), done.
remote: Total 144 (delta 6), reused 66 (delta 4), pack-reused 0
Receiving objects: 100% (144/144), 184.98 KiB | 1.71 MiB/s, done.
Resolving deltas: 100% (6/6), done.
Cloning into 'pell'...
remote: Enumerating objects: 27, done.
remote: Counting objects: 100% (27/27), done.
remote: Compressing objects: 100% (24/24), done.
remote: Total 27 (delta 2), reused 15 (delta 0), pack-reused 0
Receiving objects: 100% (27/27), 695.63 KiB | 2.27 MiB/s, done.
Resolving deltas: 100% (2/2), done.
C

remote: Enumerating objects: 184, done.
remote: Counting objects: 100% (184/184), done.
remote: Compressing objects: 100% (157/157), done.
remote: Total 184 (delta 7), reused 133 (delta 4), pack-reused 0
Receiving objects: 100% (184/184), 320.48 KiB | 625.00 KiB/s, done.
Resolving deltas: 100% (7/7), done.
Cloning into 'react-360'...
remote: Enumerating objects: 866, done.
remote: Counting objects: 100% (866/866), done.
remote: Compressing objects: 100% (734/734), done.
remote: Total 866 (delta 168), reused 484 (delta 94), pack-reused 0
Receiving objects: 100% (866/866), 70.05 MiB | 4.22 MiB/s, done.
Resolving deltas: 100% (168/168), done.
Cloning into 'dom-to-image'...
remote: Enumerating objects: 6582, done.
remote: Counting objects: 100% (6582/6582), done.
remote: Compressing objects: 100% (4698/4698), done.
remote: Total 6582 (delta 1456), reused 6550 (delta 1451), pack-reused 0
Receiving objects: 100% (6582/6582), 7.77 MiB | 1.53 MiB/s, done.
Resolving deltas: 100% (1456/1456), do

Cloning into 'x-spreadsheet'...
remote: Enumerating objects: 170, done.
remote: Counting objects: 100% (170/170), done.
remote: Compressing objects: 100% (152/152), done.
remote: Total 170 (delta 28), reused 69 (delta 14), pack-reused 0
Receiving objects: 100% (170/170), 547.73 KiB | 2.19 MiB/s, done.
Resolving deltas: 100% (28/28), done.
Cloning into 'standard'...
remote: Enumerating objects: 116, done.
remote: Counting objects: 100% (116/116), done.
remote: Compressing objects: 100% (110/110), done.
remote: Total 116 (delta 11), reused 73 (delta 0), pack-reused 0
Receiving objects: 100% (116/116), 838.64 KiB | 2.03 MiB/s, done.
Resolving deltas: 100% (11/11), done.
Cloning into 'intl-tel-input'...
remote: Enumerating objects: 172, done.
remote: Counting objects: 100% (172/172), done.
remote: Compressing objects: 100% (148/148), done.
remote: Total 172 (delta 28), reused 105 (delta 18), pack-reused 0
Receiving objects: 100% (172/172), 663.32 KiB | 1.69 MiB/s, done.
Resolving deltas: 1

...

remote: Compressing objects: 100% (181/181), done.
remote: Total 188 (delta 12), reused 80 (delta 4), pack-reused 0
Receiving objects: 100% (188/188), 2.39 MiB | 2.44 MiB/s, done.
Resolving deltas: 100% (12/12), done.
Cloning into 'stats.js'...
remote: Enumerating objects: 26, done.
remote: Counting objects: 100% (26/26), done.
remote: Compressing objects: 100% (17/17), done.
remote: Total 26 (delta 6), reused 16 (delta 5), pack-reused 0
Receiving objects: 100% (26/26), 28.08 KiB | 575.00 KiB/s, done.
Resolving deltas: 100% (6/6), done.
Cloning into 'deck.js'...
remote: Enumerating objects: 75, done.
remote: Counting objects: 100% (75/75), done.
remote: Compressing objects: 100% (72/72), done.
remote: Total 75 (delta 9), reused 31 (delta 2), pack-reused 0
Receiving objects: 100% (75/75), 100.53 KiB | 1.00 MiB/s, done.
Resolving deltas: 100% (9/9), done.
Cloning into 'RAP'...
remote: Enumerating objects: 811, done.
remote: Counting objects: 100% (811/811), done.
remote: Compressing obje

remote: Compressing objects: 100% (388/388), done.
remote: Total 414 (delta 47), reused 154 (delta 17), pack-reused 0
Receiving objects: 100% (414/414), 1.84 MiB | 2.42 MiB/s, done.
Resolving deltas: 100% (47/47), done.
Cloning into 'Web'...
remote: Enumerating objects: 299, done.
remote: Counting objects: 100% (299/299), done.
remote: Compressing objects: 100% (295/295), done.
remote: Total 299 (delta 0), reused 120 (delta 0), pack-reused 0
Receiving objects: 100% (299/299), 831.84 KiB | 1.16 MiB/s, done.
Cloning into 'madge'...
remote: Enumerating objects: 150, done.
remote: Counting objects: 100% (150/150), done.
remote: Compressing objects: 100% (97/97), done.
remote: Total 150 (delta 1), reused 119 (delta 0), pack-reused 0
Receiving objects: 100% (150/150), 36.25 KiB | 727.00 KiB/s, done.
Resolving deltas: 100% (1/1), done.
Cloning into 'WebSlides'...
remote: Enumerating objects: 159, done.
remote: Counting objects: 100% (159/159), done.
remote: Compressing objects: 100% (150/150)

remote: Total 1766 (delta 239), reused 987 (delta 157), pack-reused 0
Receiving objects: 100% (1766/1766), 1.66 MiB | 3.73 MiB/s, done.
Resolving deltas: 100% (239/239), done.
Cloning into 'es6-promise'...
remote: Enumerating objects: 47, done.
remote: Counting objects: 100% (47/47), done.
remote: Compressing objects: 100% (44/44), done.
remote: Total 47 (delta 0), reused 16 (delta 0), pack-reused 0
Receiving objects: 100% (47/47), 77.70 KiB | 1.49 MiB/s, done.
Cloning into 'Mock'...
remote: Enumerating objects: 73, done.
remote: Counting objects: 100% (73/73), done.
remote: Compressing objects: 100% (66/66), done.
remote: Total 73 (delta 1), reused 25 (delta 0), pack-reused 0
Receiving objects: 100% (73/73), 708.53 KiB | 1.71 MiB/s, done.
Resolving deltas: 100% (1/1), done.
Cloning into 'request'...
remote: Enumerating objects: 133, done.
remote: Counting objects: 100% (133/133), done.
remote: Compressing objects: 100% (121/121), done.
remote: Total 133 (delta 9), reused 78 (delta 7),

Cloning into 'react-router-tutorial'...
remote: Enumerating objects: 83, done.
remote: Counting objects: 100% (83/83), done.
remote: Compressing objects: 100% (68/68), done.
remote: Total 83 (delta 28), reused 31 (delta 11), pack-reused 0
Receiving objects: 100% (83/83), 24.82 KiB | 4.96 MiB/s, done.
Resolving deltas: 100% (28/28), done.
Cloning into 'vue'...
remote: Enumerating objects: 662, done.
remote: Counting objects: 100% (662/662), done.
remote: Compressing objects: 100% (600/600), done.
remote: Total 662 (delta 65), reused 266 (delta 42), pack-reused 0
Receiving objects: 100% (662/662), 1.16 MiB | 3.44 MiB/s, done.
Resolving deltas: 100% (65/65), done.
Cloning into 'Framer'...
remote: Enumerating objects: 1443, done.
remote: Counting objects: 100% (1443/1443), done.
remote: Compressing objects: 100% (1352/1352), done.
remote: Total 1443 (delta 90), reused 1214 (delta 61), pack-reused 0
Receiving objects: 100% (1443/1443), 260.13 MiB | 4.08 MiB/s, done.
Resolving deltas: 100% (

Cloning into 'html5-boilerplate'...
remote: Enumerating objects: 63, done.
remote: Counting objects: 100% (63/63), done.
remote: Compressing objects: 100% (58/58), done.
remote: Total 63 (delta 4), reused 33 (delta 1), pack-reused 0
Receiving objects: 100% (63/63), 216.06 KiB | 1.69 MiB/s, done.
Resolving deltas: 100% (4/4), done.
Cloning into 'reaction'...
remote: Enumerating objects: 537, done.
remote: Counting objects: 100% (537/537), done.
remote: Compressing objects: 100% (445/445), done.
remote: Total 537 (delta 145), reused 247 (delta 71), pack-reused 0
Receiving objects: 100% (537/537), 1.58 MiB | 2.85 MiB/s, done.
Resolving deltas: 100% (145/145), done.
Cloning into 'ndb'...
remote: Enumerating objects: 83, done.
remote: Counting objects: 100% (83/83), done.
remote: Compressing objects: 100% (65/65), done.
remote: Total 83 (delta 11), reused 47 (delta 9), pack-reused 0
Receiving objects: 100% (83/83), 96.73 KiB | 1021.00 KiB/s, done.
Resolving deltas: 100% (11/11), done.
Cloni

# List commit hashes

Collect hashes of last commits

In [37]:
collected_projects = sorted([dir_ for dir_ in os.listdir(DATA_REPOS)])

# with open('repositories_commits.tsv', 'w') as f:
#     f.write(f'project\thash\n')
    
#     for project in collected_projects:
#         try:
#             commit = ! cd {DATA_REPOS}/{project} && git rev-parse HEAD
#             commit = commit[0]
            
#             print(project, '\t', commit)
#             f.write(f'{project}\t{commit}\n')

#         except Exception as e:
#             print('!!! ', project, ' ', e)

30-Days-Of-JavaScript 	 07143be3b78488dd7237c34a95694ec3fb68cfc6
30-seconds-of-interviews 	 da235b6185721161b7ebc413075b76dc70339ccf
33-js-concepts 	 297390847d8bdf70f48903c9dafc093abcfb7a12
500lines 	 fba689d101eb5600f5c8f4d7fd79912498e950e2
APlayer 	 0efdc490e1be74ff421a46e4222e10b553d3866f
AdminLTE 	 45db04f87b4c75c30252733d5f791ae87f7a8b7a
Administrative-divisions-of-China 	 a3d1a730bb5248bdb008d3cf38d8277cf54b73e3
AndroidAssetStudio 	 24d8e4fbea6e944b339ce7a81cd147fdd20c312c
AriaNg 	 fb142ad720ff258f8bc42f28d2adcafdc9dcce57
Awesome-Profile-README-templates 	 72a8f8ed3dca4829ec77c0eb0afa04d70b5e441f
Blog 	 648c47284fba9ee948cf21966fb6c9accff5a112
Chart.js 	 681ada552ec3b965d80825b13f49f20d564edcc8
ChineseBQB 	 7e22c92c09dd1cc0feb3773c625a4306656f361d
ChromeAppHeroes 	 48cf8476ce8f1229cc01ee554db6e9ff2b90365e
CodeMirror 	 91a12722aafbf7398d93e906e1ced8d750b5cef3
Crash-Course-Computer-Science-Chinese 	 3f39367c04869f9559f43df83bedc639621fc727
DPlayer 	 808dd623d6b3facf321f27f9358c5fe

drawio-desktop 	 8d646aca148d0c89d078236c505317ed9daaf18c
driver.js 	 0b31fb753d01cdebff5c9b4feb8c466586b387d0
ducks-modular-redux 	 60390d09e6c5606d5fd4d5f1b2ed4c02572e9692
editor.md 	 63786e671e2c1a1fd2be25b54a8910cd3bbc7c0a
egg 	 192d42bb68713a164252b18f6ffd5dab5371c992
ejs 	 e4180b4fa2dd0e06d811f2c155f9d993ee9d8edd
elasticsearch-head 	 2d51fecac2980d350fcd3319fd9fe2999f63c9db
electron-packager 	 42aa5db3012546ce12302bb114ef03fe84f3a4f1
electron-vue 	 8d4ed607d65300381a8f47d97923eb07832b1a9a
eleventy 	 6c664cc98a3449e46f3091eee76672a79a650243
ember.js 	 9d0ed5bbb8bf112e72be378575954f4624730798
emoji-cheat-sheet 	 113a0ff3133b530f2a255ab168f19b0376e0c1f8
engine 	 b1367a07fa177e51146d8361bdb0d6a84a2f79a8
enzyme 	 c8c74a4753bd874edf6eac26bbf1b304a88e023a
eruda 	 948a0eacdd867262a7cf9bb38e217e930e6f7513
es6-cheatsheet 	 a03267ceaf4e445aeca078b924ba92d6456d6b6b
es6-promise 	 f97e2666e6928745c450752e74213d2438b48b4c
eslint-plugin-react 	 e5b9f3543fd7aa3c50099f50f98e8b185679712f
ethereumbo

next.js 	 58755e6d25a9bdab97071cf0793fdd64127e658c
ng-file-upload 	 a4c4187c11bcc1a7eb81cf73171ad0110ac2e2f6
nginxconfig.io 	 98cb59bbdf6f162f811f41eabb095b53ccf9e7b4
nightwatch 	 af22b8729597245413bff1254462b34538c8f8c3
noVNC 	 2c48df45605f7429ea30eeffd0acb0e23e10f2dc
nock 	 61d91447eddfb2ba792034502bd15be3dc81cf2e
node 	 df2fe87c69455da3d1516f3eccdea001c06af583
node-config 	 98f2fc9bd634f6dab61bc1a0003de4dbf8f9a9ad
node-cron 	 bf88cf2e4e1c0ca8f979467caa0f76ff84086292
node-elm 	 21476dddcc3c04e80ddcfa4a9eb01243a0e1fc64
node-glob 	 3bfec21dd180ddf4672880176ad33af6296a167e
node-http-proxy 	 9b96cd725127a024dabebec6c7ea8c807272223d
node-inspector 	 79e01c049286374f86dd560742a614019c02402f
node-jsonwebtoken 	 74d5719bd03993fcf71e3b176621f133eb6138c0
node-notifier 	 52ad27b3c28c0bf27afdbd4b90033dd6fa2b10af
node-qrcode 	 f08fd572d7cca92c8b9d71b24cebccf61663d4a6
node-restify 	 71c7f4965342c13cac55847f87149cc34c1ad566
nodebestpractices 	 6f6acbccb78402594e654b79f689e8537964cb95
nodemon 	 26db

toastr 	 50092cc604850a16c985520b63df184d3e0b4086
traceur-compiler 	 caa7b751d5150622e13cdd18865e09681d8c6691
trianglify 	 0d469f288fa72b7dce91ea36a58a1261487953ff
trilium 	 51348cfbad5f29bff45d995e487c78402ab0530f
truffle 	 2e357fbddcbd133c8ad9f14430fb5b574fc84fe8
tui.calendar 	 4d222ce7893ca2b9574e17fa8946347ca54cddd3
two.js 	 921c8c0200079dab4d5f802f29b01a78700a9c80
typed.js 	 a8c8686576dc52d416d1e734b3b3eeffcc28bd93
uBlock 	 58f897d48d4aa5cd45ddf0aeba305f5a518a0463
udemy-downloader-gui 	 5c4f70d1b9a160dd9ed28a082c768c44356e9545
ueditor 	 e13fa584730b7b1a2a17103f69d5ea3e3a3ce63f
ui-grid 	 863c820267ea71fecbcbdf1d2e9e6d83a8fe500d
unfetch 	 4dabeb6d4968587c5d35b520dd176414325bc5f4
uppy 	 0dbec6025713914c6e66c6c78c452ca7086b103e
uptime-kuma 	 733d0af75f6cec38b540f44143899358df7307c7
uuid 	 27b9db1f31a19eb1ca3ddca3ae4976b05a1ae869
validator.js 	 47ee5ad64cf5c684c841b59110af4e221b74945c
vant-weapp 	 104691e18f85610d325a8c82cf7aa1270a7b5ce7
vega 	 9c29632115594faa563a7694e7ba345f44ea11cb


Checkout commits

In [40]:
with open('repositories_commits.tsv', 'r') as f:
    for line in f.readlines()[1:]:
        directory, commit = line.split('\t')
        ! cd {DATA_REPOS}/{directory} && git checkout {commit}


Note: switching to '07143be3b78488dd7237c34a95694ec3fb68cfc6'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by using -c with the switch command. Example:

  git switch -c <new-branch-name>

Or undo this operation with:

  git switch -

Turn off this advice by setting config variable advice.detachedHead to false

HEAD is now at 07143be paypal link has been added
Note: switching to 'da235b6185721161b7ebc413075b76dc70339ccf'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
do so (now or lat

Note: switching to '48cf8476ce8f1229cc01ee554db6e9ff2b90365e'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by using -c with the switch command. Example:

  git switch -c <new-branch-name>

Or undo this operation with:

  git switch -

Turn off this advice by setting config variable advice.detachedHead to false

HEAD is now at 48cf847 ok
Note: switching to '91a12722aafbf7398d93e906e1ced8d750b5cef3'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by using -c with the

Note: switching to 'f4ade18998a48347b7f35a0f082d063d00ed79f9'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by using -c with the switch command. Example:

  git switch -c <new-branch-name>

Or undo this operation with:

  git switch -

Turn off this advice by setting config variable advice.detachedHead to false

HEAD is now at f4ade18 chore(deps): update dependency mini-css-extract-plugin to v2.4.4 [skip netlify] (#3403)
Note: switching to 'f3295e47b4ed745becb4710e9ac9375531b4b2c4'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new b

Note: switching to '9bab05cd67c4fd8748fa71f6fcf2bcf3408644f4'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by using -c with the switch command. Example:

  git switch -c <new-branch-name>

Or undo this operation with:

  git switch -

Turn off this advice by setting config variable advice.detachedHead to false

HEAD is now at 9bab05c Merge pull request #150 from jwmann/feature/update-nodejs-example
Note: switching to '9d91fd47eb59c11a80d570d4ea0beaa59cfc71bf'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commit

Note: switching to '54ed78b00d7d8209790dd167dece747bfe9c5b88'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by using -c with the switch command. Example:

  git switch -c <new-branch-name>

Or undo this operation with:

  git switch -

Turn off this advice by setting config variable advice.detachedHead to false

HEAD is now at 54ed78b can't figure this out rn, would come later
Note: switching to 'bbcdbc13b3d7864369f0d09a7c089277dec946da'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
d

...

Note: switching to 'caa7b751d5150622e13cdd18865e09681d8c6691'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by using -c with the switch command. Example:

  git switch -c <new-branch-name>

Or undo this operation with:

  git switch -

Turn off this advice by setting config variable advice.detachedHead to false

HEAD is now at caa7b75 Use universal method of finding the global object (#2132)
Note: switching to '0d469f288fa72b7dce91ea36a58a1261487953ff'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you cr

Note: switching to '733d0af75f6cec38b540f44143899358df7307c7'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by using -c with the switch command. Example:

  git switch -c <new-branch-name>

Or undo this operation with:

  git switch -

Turn off this advice by setting config variable advice.detachedHead to false

HEAD is now at 733d0af update to 1.10.1
Note: switching to '27b9db1f31a19eb1ca3ddca3ae4976b05a1ae869'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by usi

Note: switching to 'e6d74341c1e3e1091f0841012d303e092c6f2676'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by using -c with the switch command. Example:

  git switch -c <new-branch-name>

Or undo this operation with:

  git switch -

Turn off this advice by setting config variable advice.detachedHead to false

HEAD is now at e6d7434 Merge branch 'main' of github.com:bencodezen/vue-enterprise-boilerplate into main
Note: switching to '98399b55c6f1da4197840ba76189795b3e95be0f'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch 

Note: switching to '298503082f1ff758ef8ec5dbf5f91f5d8bdd0333'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by using -c with the switch command. Example:

  git switch -c <new-branch-name>

Or undo this operation with:

  git switch -

Turn off this advice by setting config variable advice.detachedHead to false

HEAD is now at 2985030 Update README.md
Note: switching to '530a59ddb3a7a485316dceba68a8c2ced3fb648b'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by usi

Note: switching to '5991c3548404e441129a16887e6a15250722a960'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by using -c with the switch command. Example:

  git switch -c <new-branch-name>

Or undo this operation with:

  git switch -

Turn off this advice by setting config variable advice.detachedHead to false

HEAD is now at 5991c35 [doc] Fix nits
Note: switching to 'dbf462b26b219acea22a9252fb74afad2717a353'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by using

# Extract JS files from data/repos to data/js_files

Create `data/js_files/` directory

In [43]:
create_dir_if_not_exists(DATA_JS_FILES)

Copy files with plain '.js' extension from `data/repos` to `data/js_files`

In [44]:
repos_files = [
    os.path.join(path, name) 
    for path, _, files in os.walk(DATA_REPOS)
    for name in files
    if name.endswith('.js') and name.count('.') == 1
]

def process_file(file):
    src = file
    dst = os.path.join(DATA_JS_FILES, file.lstrip(DATA_REPOS).replace('/', '_'))

    if os.path.exists(src):
        shutil.copy(src, dst)


with multiprocessing.Pool(processes=os.cpu_count() - 1) as pool:
    for _ in tqdm.tqdm(pool.imap_unordered(process_file, repos_files)):
        pass


print('JS files in repositories: ', len([_ for path, _, files in os.walk(DATA_JS_FILES) for name in files]))

166142it [01:58, 1407.16it/s]


JS files in repositories:  166129


Now `data/repos` directory could be removed 

# Extract functions from js files

__!NB: You should have [node.js](https://nodejs.org/en/) and [esprima](https://www.npmjs.com/package/esprima) npm package installed__

Create `data/funcs/` directory

In [46]:
create_dir_if_not_exists(DATA_FUNCS)

[Errno 17] File exists: 'data/funcs/'


Extract functions from JS files

In [47]:
js_files = [os.path.join(path, name) for path, _, files in os.walk(DATA_JS_FILES) for name in files]


def process_file(file):
    input_file = file
    output_file = os.path.join(DATA_FUNCS, file.lstrip(DATA_JS_FILES))
    
    command = [
        'node',
        'scripts/parse_functions.js',
        input_file,
        output_file
    ]

    subprocess.run(command)


with multiprocessing.Pool(processes=os.cpu_count() - 1) as pool:
    for _ in tqdm.tqdm(pool.imap_unordered(process_file, js_files), total=len(js_files)):
        pass


100%|██████████| 166129/166129 [2:13:37<00:00, 20.72it/s]  


# Generate obfuscated functions

Create `data/obfuscated_funcs/` directory with subdirectories

In [4]:
create_dir_if_not_exists(DATA_OBFUSCATED_FUNCS)

In [5]:
OBFUSCATORS = ['defendjs', 'jscrewit', 'gnirts', 'javascript-obfuscator',
               'jsobfu', 'jfogs', 'closure', 'uglifyjs', 'original']


for obfuscator in OBFUSCATORS:
    create_dir_if_not_exists(os.path.join(DATA_OBFUSCATED_FUNCS, obfuscator))


Randomly assign obfuscator to function

In [6]:
len([os.path.join(path, name) for path, _, files in os.walk(DATA_FUNCS) for name in files])

787127

In [7]:
random.seed(144)


functions = sorted([os.path.join(path, name) for path, _, files in os.walk(DATA_FUNCS) for name in files])
random.shuffle(functions)

In [8]:
OBFUSCATOR_TO_FUNCTIONS = collections.defaultdict(list)


for i, obfuscator in enumerate(OBFUSCATORS):
    OBFUSCATOR_TO_FUNCTIONS[obfuscator] += functions[
        math.floor(len(functions) / 10 * i) : math.floor(len(functions) / 10 * (i + 1))
    ]

OBFUSCATOR_TO_FUNCTIONS['original'] += functions[math.floor(len(functions) / 10 * (i + 1)):]


print('Functions sampling results:')
for k, v in OBFUSCATOR_TO_FUNCTIONS.items():
    print(f'{k}: {len(v)}')


Functions sampling results:
defendjs: 78712
jscrewit: 78713
gnirts: 78713
javascript-obfuscator: 78712
jsobfu: 78713
jfogs: 78713
closure: 78712
uglifyjs: 78713
original: 157426


Generate obfuscated samples

In [9]:
for obfuscator in OBFUSCATORS:
    def process_file(file):
        input_file = os.path.join(os.getcwd(), file)
        output_file = os.path.join(os.getcwd(), DATA_OBFUSCATED_FUNCS, obfuscator, file.lstrip(DATA_FUNCS))

        command = ['bash', f'run_{obfuscator}.sh', input_file, output_file]
        subprocess.run(command, cwd='scripts/obfuscate/')

    def run_obfuscator():
        with multiprocessing.Pool(processes=os.cpu_count() - 1) as pool:
            for _ in tqdm.tqdm(pool.imap_unordered(process_file, OBFUSCATOR_TO_FUNCTIONS[obfuscator])):
                if obfuscator != 'original' and \
                        len(os.listdir(os.path.join(DATA_OBFUSCATED_FUNCS, obfuscator))) > 20000:
                    return

    run_obfuscator()

20230it [2:38:09,  2.13it/s]
20000it [56:07,  5.94it/s]
11314it [10:35, 17.81it/s]
20019it [1:43:23,  3.23it/s]
19998it [46:47,  7.12it/s]
18517it [22:28, 13.73it/s]
20023it [14:20:11,  2.58s/it]
19961it [31:46, 10.47it/s]
157426it [12:11, 215.25it/s]


In [10]:
# create_dir_if_not_exists(os.path.join(DATA_OBFUSCATED_FUNCS, 'original'))

# for file in functions:
#     src = file
#     dst = os.path.join(DATA_OBFUSCATED_FUNCS, 'original', file.lstrip(DATA_FUNCS))
#     shutil.copyfile(src, dst)

Make `data/obfuscated_funcs/defendjs` data structure complient with the rest of the directories

In [11]:
defendjs_functions = sorted(
    [os.path.join(path, name) 
     for path, _, files in os.walk(os.path.join(DATA_OBFUSCATED_FUNCS, 'defendjs'))
     for name in files]
)


print('Found defendjs files: ', len(defendjs_functions))


for file in defendjs_functions:
    src = file
    dst = os.path.join(os.path.dirname(os.path.dirname(file)), os.path.basename(file))

    try:
        if os.path.join(DATA_OBFUSCATED_FUNCS, 'defendjs') not in dst:
            continue

        with open(src, 'rb') as fr:
            content = fr.read()

        shutil.rmtree(os.path.dirname(src))

        with open(dst, 'wb') as fw:
            fw.write(content)

    except Exception as e:
        print(e)


Found defendjs files:  20004


In [12]:
defendjs_functions = sorted(
    [os.path.join(path, name) 
     for path, _, files in os.walk(os.path.join(DATA_OBFUSCATED_FUNCS, 'defendjs'), topdown=False)
     for name in files]
)

print('Moved defendjs files: ', len(defendjs_functions))

Moved defendjs files:  20004


# Extract features

In [13]:
create_dir_if_not_exists(DATA_AST_FEATURES)

In [14]:
for obfuscator in OBFUSCATORS:
    create_dir_if_not_exists(os.path.join(DATA_AST_FEATURES, obfuscator))

In [15]:
import sys
sys.path.extend(['/Users/grigory/Documents/2019/PyProj/ast_to_neo4j/'])


from converter import converter


obfuscated_functions = sorted(
    [os.path.join(path, name) for path, _, files in os.walk(DATA_OBFUSCATED_FUNCS) for name in files]
)


def process_file(file):
    input_file = file
    obfusactor = os.path.dirname(input_file).split('/')[-1]
    output_file = os.path.join(DATA_AST_FEATURES, obfusactor, file.lstrip(DATA_OBFUSCATED_FUNCS).replace('/', '_'))

    try:
        features_extractor = converter.AstToCsvConverter()
        features_extractor.parse(path=input_file)
        features_extractor.convert()
        features_extractor.save_features(path=output_file)
 
    except Exception as e:
        print(e)


with multiprocessing.Pool(processes=os.cpu_count() - 1) as pool:
    for _ in tqdm.tqdm(pool.imap_unordered(process_file, obfuscated_functions), total=len(obfuscated_functions)):
        pass




  7%|▋         | 21298/317448 [19:22<6:07:10, 13.44it/s] 

Expecting value: line 1 column 1 (char 0)


  7%|▋         | 21618/317448 [19:44<5:34:29, 14.74it/s]

Expecting value: line 1 column 1 (char 0)
Expecting value: line 1 column 1 (char 0)


  7%|▋         | 21621/317448 [19:44<5:51:01, 14.05it/s]

...

Expecting value: line 1 column 1 (char 0)


 93%|█████████▎| 296708/317448 [8:01:44<18:35, 18.60it/s]

Expecting value: line 1 column 1 (char 0)


100%|██████████| 317448/317448 [8:18:58<00:00, 10.60it/s]


NameError: name 'run' is not defined

In [46]:
ast_features = sorted(
    [os.path.join(path, name) for path, _, files in os.walk(DATA_AST_FEATURES) for name in files]
)


len(ast_features)

316053

# Create train and test dataframes

Create train and test samples

In [47]:
from sklearn.model_selection import train_test_split


train_ast, test_ast = train_test_split(ast_features, test_size=0.3, random_state=11)

print('Train size: ', len(train_ast))
print('Test size: ', len(test_ast))

Train size:  221237
Test size:  94816


In [ ]:
# iterate over train and get node names and node pairs


FEATURES = set()

for file_path in tqdm.tqdm(train_ast):
    try:
        with open(file_path, 'r') as f:
            data = json.load(f)
        for k_first in data.keys():
            for k_second in data[k_first].keys():
                FEATURES.add(f'{k_first};{k_second}')
    except Exception as e:
        print(e)


with open(DATA_FEATURES_JSON, 'wb') as f:
    f.write(json.dumps(sorted(list(FEATURES))).encode('utf-8'))

In [48]:
with open(DATA_FEATURES_JSON, 'rb') as f:
    FEATURES = json.loads(f.read().decode())


FEATURES = sorted([tuple(f.split(';')) for f in FEATURES])
print('Collected features count: ', len(FEATURES))

Collected features count:  778


Collect train dataset

In [49]:
dataframe_rows = []


for file in tqdm.tqdm(train_ast):
    try:
        with open(file, 'r') as f:
            data = json.load(f)

        obfuscator = os.path.dirname(file).split('/')[-1]
        feature_vector = {'file': file, 'obfuscator': obfuscator}

        for key_first, key_second in FEATURES:
            feature_vector[f'{key_first};{key_second}'] = data[key_first].get(key_second, 0)

        dataframe_rows.append(feature_vector)

    except Exception as e:
        print(e)


train_df = pd.DataFrame(dataframe_rows)
del dataframe_rows

100%|██████████| 221237/221237 [08:12<00:00, 449.38it/s]


In [52]:
pair_features = [f for f in train_df.columns if 'node_pairs;' in f]
single_features = [f for f in train_df.columns if 'nodes;' in f]
other_features = [f for f in train_df.columns if f not in pair_features + single_features]

In [53]:
def supplement_features(df: pd.DataFrame):
    df[single_features] = df[single_features].astype(int)
    df[pair_features] = df[pair_features].astype(int)

    df['sum'] = df[single_features].sum(axis=1)
    df = df[df['sum'] >= 25].copy(deep=True)
    del df['sum']

    df['v_types'] = df[single_features].astype(bool).sum(axis=1) / len(single_features)
    df['e_types'] = df[pair_features].astype(bool).sum(axis=1) / len(pair_features)

    df[single_features] = (df[single_features].to_numpy().T / df[single_features].to_numpy().sum(axis=1)).T
    df[pair_features] = (df[pair_features].to_numpy().T / df[pair_features].to_numpy().sum(axis=1)).T

    return df


In [54]:
train_df = supplement_features(train_df)
print('Train dataset: ', train_df.shape)

Train dataset:  (177028, 782)


Save train dataframe to `data/train.csv`

In [60]:
train_df.to_csv('data/train.csv', index=False)

Collect test dataframe

In [56]:
dataframe_rows = []


for file in tqdm.tqdm(test_ast):
    try:
        with open(file, 'r') as f:
            data = json.load(f)

        obfuscator = os.path.dirname(file).split('/')[-1]
        feature_vector = {'file': file, 'obfuscator': obfuscator}

        for key_first, key_second in FEATURES:
            feature_vector[f'{key_first};{key_second}'] = data[key_first].get(key_second, 0)

        dataframe_rows.append(feature_vector)

    except Exception as e:
        print(e)


test_df = pd.DataFrame(dataframe_rows)
del dataframe_rows

100%|██████████| 94816/94816 [03:47<00:00, 416.95it/s]


In [57]:
test_df = supplement_features(test_df)
print('Test dataset: ', test_df.shape)

Test dataset:  (75734, 782)


Save test dataframe to `data/test.csv`

In [61]:
test_df.to_csv('data/test.csv', index=False)